<a href="https://colab.research.google.com/github/PlushyWushy/Rachel/blob/main/Rachel_Full_CIFAR_10.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install tensorflow==2.15.0 numpy==2.0.2 tqdm==4.67.1
!pip install tensorflow-addons==0.23.0


INFO: pip is looking at multiple versions of tensorflow to determine which version is compatible with other requirements. This could take a while.
ERROR: Cannot install numpy==2.0.2 and tensorflow==2.15.0 because these package versions have conflicting dependencies.

The conflict is caused by:
    The user requested numpy==2.0.2
    tensorflow 2.15.0 depends on numpy<2.0.0 and >=1.23.5

To fix this you could try to:
1. loosen the range of package versions you've specified
2. remove package versions to allow pip to attempt to solve the dependency conflict

ERROR: ResolutionImpossible: for help visit https://pip.pypa.io/en/latest/topics/dependency-resolution/#dealing-with-dependency-conflicts
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 611.8/611.8 kB 33.2 MB/s eta 0:00:00
  Attempting uninstall: typeguard
    Found existing installation: typeguard 4.4.2
    Uninstalling typeguard-4.4.2:
      Successfully uninstalled typeguard-4.4.2
ERROR: pip's dependency resolver does not currently tak

In [ ]:
#RACHEL FULL CIFAR BENCHMARK
import sys
sys.setrecursionlimit(100000)  # Increase recursion limit

import tensorflow as tf
import numpy as np
from tensorflow.keras.datasets import cifar10
from tqdm import tqdm

# ------------------------------------------------------------------------------
# GPU Setup: Enable Mixed Precision and XLA for A100 Optimization
# ------------------------------------------------------------------------------
# Enable XLA JIT compilation
tf.config.optimizer.set_jit(True)

# Enable mixed precision training for faster FP16 operations (TF 2.15.0)
from tensorflow.keras.mixed_precision import set_global_policy
set_global_policy("mixed_float16")
print("Global mixed precision policy:", tf.keras.mixed_precision.global_policy())

# Mixed precision test: create a couple of float16 tensors and perform an op.
a = tf.constant([1.0, 2.0, 3.0], dtype=tf.float16)
b = tf.constant([4.0, 5.0, 6.0], dtype=tf.float16)
c = a + b
print("Test tensor c dtype (should be float16):", c.dtype)

# Use MirroredStrategy for distributed GPU training.
strategy = tf.distribute.MirroredStrategy()
print("Running on GPU with Mixed Precision and XLA enabled.")

# Set seeds for reproducibility.
tf.random.set_seed(42)
np.random.seed(42)

# =============================================================================
# 1. Data Loading and Preparation (Full CIFAR-10)
# =============================================================================
(x_train, y_train), (x_test, y_test) = cifar10.load_data()
y_train = np.squeeze(y_train).astype(np.int32)
y_test  = np.squeeze(y_test).astype(np.int32)

# Use full CIFAR-10 (10 classes)
x_train = x_train.astype(np.float32) / 255.0
x_test  = x_test.astype(np.float32) / 255.0

# Use the last 5000 examples of training for validation.
num_val = 5000
x_val = x_train[-num_val:]
y_val = y_train[-num_val:]
x_train = x_train[:-num_val]
y_train = y_train[:-num_val]

img_shape = (32, 32, 3)
num_classes = 10
batch_size = 128  # Batch size set to 1024

def make_dataset(x, y, shuffle=False):
    ds = tf.data.Dataset.from_tensor_slices((x, y))
    if shuffle:
        ds = ds.shuffle(buffer_size=10000, seed=42)
    # Optionally add data augmentation with ds.map(...)
    return ds.batch(batch_size).cache().prefetch(tf.data.AUTOTUNE)

train_ds = make_dataset(x_train, y_train, shuffle=True)
val_ds   = make_dataset(x_val, y_val, shuffle=False)
test_ds  = make_dataset(x_test, y_test, shuffle=False)

# =============================================================================
# 2. RL Controller with Actor–Critic (Expanded Candidate Blocks)
# =============================================================================
max_new_layers = 3
initial_temperature = 1.5
decay_rate = 0.95

class RLController(tf.keras.Model):
    def __init__(self, max_new_layers=5, lstm_units=64):
        super().__init__()
        self.max_new_layers = max_new_layers
        self.lstm = tf.keras.layers.LSTM(lstm_units, return_sequences=True)
        self.logits_presence = tf.keras.layers.Dense(2)
        self.logits_type     = tf.keras.layers.Dense(2)
        self.logits_units    = tf.keras.layers.Dense(241)

    def call(self, inputs, temperature=1.0, training=False):
        # Use a dummy sequence to generate candidate tokens.
        dummy_seq = tf.zeros((tf.shape(inputs)[0], self.max_new_layers, 16))
        lstm_out = self.lstm(dummy_seq)
        logits0 = self.logits_presence(lstm_out) / temperature
        logits1 = self.logits_type(lstm_out) / temperature
        logits2 = self.logits_units(lstm_out) / temperature
        return logits0, logits1, logits2

class OptimizedControllerPolicy:
    def __init__(self, max_new_layers=5, lstm_units=64, lr=1e-3):
        self.max_new_layers = max_new_layers
        self.actor = RLController(max_new_layers, lstm_units)
        self.critic = tf.keras.Sequential([
            tf.keras.layers.Flatten(),
            tf.keras.layers.Dense(64, activation='relu'),
            tf.keras.layers.Dense(1)
        ])
        self.optimizer = tf.keras.optimizers.Adam(lr)

    def sample_tokens_from_input(self, dummy_input, temperature=1.0):
        pres_logits, type_logits, units_logits = self.actor(dummy_input, temperature=temperature, training=True)
        pres_probs  = tf.nn.softmax(pres_logits, axis=-1)
        type_probs  = tf.nn.softmax(type_logits, axis=-1)
        units_probs = tf.nn.softmax(units_logits, axis=-1)
        bs = tf.shape(dummy_input)[0]

        # Sample presence
        pres_samples = tf.random.categorical(tf.math.log(tf.reshape(pres_probs, [-1, 2])), 1)
        pres_samples = tf.reshape(pres_samples, [bs, self.max_new_layers])
        pres_samples = tf.cast(pres_samples, tf.int32)

        # Sample block type
        type_samples = tf.random.categorical(tf.math.log(tf.reshape(type_probs, [-1, 2])), 1)
        type_samples = tf.reshape(type_samples, [bs, self.max_new_layers])
        type_samples = tf.cast(type_samples, tf.int32)

        # Sample block units
        units_samples = tf.random.categorical(tf.math.log(tf.reshape(units_probs, [-1, 241])), 1)
        units_samples = tf.reshape(units_samples, [bs, self.max_new_layers])
        units_samples = tf.cast(units_samples, tf.int32)

        tokens = tf.stack([pres_samples, type_samples, units_samples], axis=2)

        def gather_logp(logits, samples):
            b = tf.shape(logits)[0]
            ml = tf.shape(logits)[1]
            indices = tf.stack([
                tf.repeat(tf.range(b), ml),
                tf.tile(tf.range(ml), [b]),
                tf.reshape(tf.stop_gradient(samples), [-1])
            ], axis=1)
            gathered = tf.gather_nd(tf.nn.log_softmax(logits, axis=-1), indices)
            return tf.reshape(gathered, [b, ml])

        pres_logp = gather_logp(pres_logits, pres_samples)
        type_logp = gather_logp(type_logits, type_samples)
        units_logp = gather_logp(units_logits, units_samples)
        logp = tf.reduce_sum(pres_logp + type_logp + units_logp, axis=1)
        return tokens, logp

    def sample_tokens(self, batch_size=1, temperature=1.0):
        dummy_input = tf.random.normal((batch_size, self.max_new_layers, 16), mean=0.0, stddev=1.5)
        return self.sample_tokens_from_input(dummy_input, temperature=temperature)

    def update_policy(self, dummy_input, rewards, temperature=1.0):
        with tf.GradientTape() as tape:
            _, logp = self.sample_tokens_from_input(dummy_input, temperature=temperature)
            # Cast critic output to float32 and compute advantage.
            value_pred = tf.cast(tf.squeeze(self.critic(dummy_input), axis=1), tf.float32)
            advantage = rewards - value_pred
            # Cast advantage to the same dtype as logp (i.e. float16) to avoid type mismatch.
            advantage = tf.cast(advantage, logp.dtype)
            advantage = tf.expand_dims(tf.stop_gradient(advantage), axis=1)

            actor_loss = -tf.reduce_mean(logp * advantage)
            # Cast actor_loss to float32 so both losses are the same type.
            actor_loss = tf.cast(actor_loss, tf.float32)
            critic_loss = tf.reduce_mean(tf.square(rewards - value_pred))
            total_loss = actor_loss + 0.5 * critic_loss

        vars_to_train = self.actor.trainable_variables + self.critic.trainable_variables
        grads = tape.gradient(total_loss, vars_to_train)
        self.optimizer.apply_gradients(zip(grads, vars_to_train))

controller_policy = OptimizedControllerPolicy(max_new_layers, lstm_units=64, lr=1e-3)
prev_candidate_tokens = np.empty((0, 3), dtype=np.int32)

# =============================================================================
# 3. Decode Full Candidate to Build a Subnetwork (Optimized for GPU)
# =============================================================================
def decode_incremental_architecture(old_tokens, new_tokens):
    active = np.where(new_tokens[:, 0] == 1)[0]
    num_new = active[-1] + 1 if active.size > 0 else 0
    return np.concatenate([old_tokens, new_tokens[:num_new]], axis=0)

def decode_full_candidate(candidate_tokens, dropout_rate=0.3):
    with strategy.scope():
        inputs = tf.keras.Input(shape=img_shape)
        x = tf.keras.layers.RandomFlip("horizontal")(inputs)
        x = tf.keras.layers.RandomTranslation(0.1, 0.1)(x)

        for tok in candidate_tokens:
            if tok[0] == 0:
                continue
            block_type = tok[1]
            block_size = int(tok[2]) + 16

            if block_type == 0:
                x = tf.keras.layers.Conv2D(block_size, kernel_size=3, padding='same',
                                           kernel_regularizer=tf.keras.regularizers.l2(1e-4))(x)
                x = tf.keras.layers.BatchNormalization()(x)
                x = tf.keras.layers.Activation('relu')(x)
                x = tf.keras.layers.Dropout(dropout_rate)(x)
                if x.shape[1] is not None and x.shape[1] >= 2:
                    x = tf.keras.layers.MaxPooling2D(pool_size=2)(x)
            else:
                # Simple residual block
                shortcut = x
                x = tf.keras.layers.Conv2D(block_size, kernel_size=3, padding='same',
                                           kernel_regularizer=tf.keras.regularizers.l2(1e-4))(x)
                x = tf.keras.layers.BatchNormalization()(x)
                x = tf.keras.layers.Activation('relu')(x)
                x = tf.keras.layers.Dropout(dropout_rate)(x)

                x = tf.keras.layers.Conv2D(block_size, kernel_size=3, padding='same',
                                           kernel_regularizer=tf.keras.regularizers.l2(1e-4))(x)
                x = tf.keras.layers.BatchNormalization()(x)

                if shortcut.shape[-1] != block_size:
                    shortcut = tf.keras.layers.Conv2D(block_size, kernel_size=1, padding='same',
                                                      kernel_regularizer=tf.keras.regularizers.l2(1e-4))(shortcut)

                x = tf.keras.layers.Add()([x, shortcut])
                x = tf.keras.layers.Activation('relu')(x)
                x = tf.keras.layers.Dropout(dropout_rate)(x)
                if x.shape[1] is not None and x.shape[1] >= 2:
                    x = tf.keras.layers.MaxPooling2D(pool_size=2)(x)

        if len(x.shape) > 2:
            x = tf.keras.layers.Flatten()(x)

        outputs = tf.keras.layers.Dense(num_classes, dtype='float32')(x)
        model = tf.keras.Model(inputs=inputs, outputs=outputs)
    return model

# =============================================================================
# 4. Adaptive Candidate Training Duration (Epoch decider)
# =============================================================================
def ideal_epochs(num_layers, base_epochs=200):
    return base_epochs + 10 * num_layers

def lr_scheduler(epoch, lr):
    return lr * 0.95

def train_candidate_model(model, epochs):
    with strategy.scope():
        model.compile(optimizer=tf.keras.optimizers.Adam(1e-3),
                      loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
                      metrics=['accuracy'])
    print("Training candidate model for up to", epochs, "epochs with early stopping...")
    early_stop = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10,
                                                  min_delta=0.001, restore_best_weights=True)
    callbacks = [tf.keras.callbacks.LearningRateScheduler(lr_scheduler), early_stop]
    history = model.fit(train_ds, epochs=epochs, verbose=1,
                        validation_data=val_ds, callbacks=callbacks)
    loss, acc = model.evaluate(train_ds, verbose=1)
    return loss, acc

def evaluate_candidate_model(model):
    loss, acc = model.evaluate(val_ds, verbose=1)
    return loss, acc

# =============================================================================
# 5. Mixture Loss (Utility function)
# =============================================================================
def mixture_loss(mixture_logits, ensemble_preds, y_true):
    weights = tf.nn.softmax(mixture_logits)
    weighted_preds = tf.zeros_like(ensemble_preds[0])
    for w, pred in zip(tf.unstack(weights), ensemble_preds):
        weighted_preds += w * pred
    loss = tf.reduce_mean(tf.keras.losses.sparse_categorical_crossentropy(y_true, weighted_preds, from_logits=True))
    return loss

# Quick test of mixture loss (optional demonstration)
def test_convex_optimization():
    print("\n--- Testing Convex Mixture Optimization ---")
    dummy_preds = [tf.random.uniform((4, num_classes), minval=-1, maxval=1) for _ in range(3)]
    dummy_y = tf.constant([1, 0, 1, 0], dtype=tf.int32)
    mixture_logits_test = tf.Variable(tf.zeros([3]), name="mixture_logits_test", trainable=True)
    optimizer_test = tf.keras.optimizers.Adam(1e-3)
    initial_loss = mixture_loss(mixture_logits_test, dummy_preds, dummy_y)
    print("Initial dummy mixture loss:", initial_loss.numpy())
    for epoch in range(10):
        with tf.GradientTape() as tape:
            loss_val = mixture_loss(mixture_logits_test, dummy_preds, dummy_y)
        grads = tape.gradient(loss_val, [mixture_logits_test])
        optimizer_test.apply_gradients(zip(grads, [mixture_logits_test]))
        print(f"Epoch {epoch+1}: dummy loss {loss_val.numpy()}")
    final_weights = tf.nn.softmax(mixture_logits_test).numpy()
    print("Final dummy mixture weights:", final_weights)
    print("--- Convex Mixture Optimization Test Completed ---\n")

test_convex_optimization()

# =============================================================================
# 6. Main RL with Extended Candidate Search, Adaptive Training, & Logging
# =============================================================================
num_candidates = 5
ensemble = []
prev_tokens = np.empty((0, 3), dtype=np.int32)
prev_model = None
prev_obj = None
iterations = 10
safety_margin = 0.01
safety_net_count = 0

for it in range(iterations):
    print(f"\n--- RL Iteration {it+1}/{iterations} ---")
    current_temperature = initial_temperature * (decay_rate ** it)
    dummy_input = tf.random.normal((num_candidates, max_new_layers, 16), mean=0.0, stddev=1.5)
    tokens_batch, logp_batch = controller_policy.sample_tokens_from_input(dummy_input, temperature=current_temperature)

    rewards = []
    candidate_tokens_list = []
    candidate_models = []

    for j in range(num_candidates):
        candidate_tokens = decode_incremental_architecture(prev_tokens, tokens_batch[j].numpy())
        num_layers = candidate_tokens.shape[0]
        dropout_rate = max(0.1, 0.3 - 0.02 * num_layers)
        print(f"\nCandidate {j+1}: layers = {num_layers}, dropout_rate = {dropout_rate:.2f}")

        model_candidate = decode_full_candidate(candidate_tokens, dropout_rate=dropout_rate)
        model_candidate.summary()
        epochs_to_train = ideal_epochs(num_layers)
        tr_loss, tr_acc = train_candidate_model(model_candidate, epochs=epochs_to_train)

        # Evaluate Candidate in Ensemble Context
        if len(ensemble) == 0:
            val_loss, val_acc = evaluate_candidate_model(model_candidate)
            print(f"  Standalone Evaluation -> Train loss: {tr_loss:.4f}, acc: {tr_acc:.4f} | "
                  f"Val loss: {val_loss:.4f}, acc: {val_acc:.4f}")
            obj = val_loss
        else:
            candidate_ensemble = ensemble + [model_candidate]
            mixture_logits_temp = tf.Variable(tf.zeros([len(candidate_ensemble)]), trainable=True)
            optimizer_temp = tf.keras.optimizers.Adam(1e-3)
            candidate_epochs_mix = 10
            print(f"  Evaluating Candidate {j+1} with current ensemble of {len(ensemble)} models...")

            for epoch in range(candidate_epochs_mix):
                total_loss = 0.0
                batches = 0
                for x_batch, y_batch in val_ds:
                    ensemble_preds = [m(x_batch, training=False) for m in candidate_ensemble]
                    with tf.GradientTape() as tape:
                        loss_val = mixture_loss(mixture_logits_temp, ensemble_preds, y_batch)
                    grads = tape.gradient(loss_val, [mixture_logits_temp])
                    optimizer_temp.apply_gradients(zip(grads, [mixture_logits_temp]))
                    total_loss += loss_val.numpy()
                    batches += 1
                avg_loss = total_loss / batches
                print(f"    Mixture optimization epoch {epoch+1}/{candidate_epochs_mix}, loss: {avg_loss:.4f}")

            # Final validation mixture loss
            total_loss = 0.0
            batches = 0
            for x_batch, y_batch in val_ds:
                ensemble_preds = [m(x_batch, training=False) for m in candidate_ensemble]
                loss_val = mixture_loss(mixture_logits_temp, ensemble_preds, y_batch)
                total_loss += loss_val.numpy()
                batches += 1
            final_val_loss = total_loss / batches
            print(f"  Combined Evaluation -> Final validation loss with candidate: {final_val_loss:.4f}")
            obj = final_val_loss

        r = -obj
        print(f"  Objective: {obj:.4f} | Reward: {r:.4f}")
        rewards.append(r)
        candidate_tokens_list.append(candidate_tokens)
        candidate_models.append(model_candidate)

    rewards_tf = tf.cast(tf.stack(rewards), tf.float32)
    controller_policy.update_policy(dummy_input, rewards_tf, temperature=current_temperature)

    best_idx = int(np.argmax(rewards))
    best_r = rewards[best_idx]
    best_tokens_new = candidate_tokens_list[best_idx]
    best_model_new = candidate_models[best_idx]

    print(f"\nBest candidate in iteration {it+1} had reward = {best_r:.4f}")

    # Safety check
    if (prev_obj is not None) and (prev_obj > best_r + safety_margin):
        print("=> Safety-net: Reusing previous candidate.")
        safety_net_count += 1
        ensemble.append(prev_model)
    else:
        print("=> Candidate selected for ensemble.")
        ensemble.append(best_model_new)
        prev_obj = best_r
        prev_model = best_model_new
        prev_tokens = best_tokens_new

print(f"\nSafety net was used in {safety_net_count} out of {iterations} iterations.")

print("\nFinal Ensemble Architectures:")
for i, model in enumerate(ensemble):
    print(f"\nCandidate {i+1} Architecture Summary:")
    model.summary()

# =============================================================================
# 7. Optimize Mixture Weights for the Ensemble (Final Stage, Distributed)
# =============================================================================
with strategy.scope():
    mixture_logits = tf.Variable(tf.zeros([len(ensemble)]), name="mixture_logits", trainable=True)
    optimizer_mix = tf.keras.optimizers.Adam(1e-3)

# Distribute validation dataset for mixture training
dist_val_ds = strategy.experimental_distribute_dataset(val_ds)

@tf.function
def distributed_mixture_train_step(x_batch, y_batch):
    """
    Perform a single gradient update on mixture_logits in a distributed manner.
    """
    def step_fn(inputs):
        x, y = inputs
        with tf.GradientTape() as tape:
            ensemble_preds = [model(x, training=False) for model in ensemble]
            loss_val = mixture_loss(mixture_logits, ensemble_preds, y)
        grads = tape.gradient(loss_val, [mixture_logits])
        optimizer_mix.apply_gradients(zip(grads, [mixture_logits]))
        return loss_val

    per_replica_losses = strategy.run(step_fn, args=((x_batch, y_batch),))
    return strategy.reduce(tf.distribute.ReduceOp.SUM, per_replica_losses, axis=None)

epochs_mix = 50
for epoch in range(epochs_mix):
    epoch_loss = 0.0
    batches = 0
    for x_batch, y_batch in dist_val_ds:
        loss_val = distributed_mixture_train_step(x_batch, y_batch)
        epoch_loss += loss_val.numpy()
        batches += 1
    print(f"Mixture weight optimization epoch {epoch+1}/{epochs_mix}, loss: {epoch_loss / batches:.4f}")

final_weights = tf.nn.softmax(mixture_logits).numpy()
print("Optimized mixture weights:", final_weights)

# =============================================================================
# Define ensemble_predict for evaluation
# =============================================================================
def ensemble_predict(x, ensemble, mixture_weights):
    ensemble_preds = [model(x, training=False) for model in ensemble]
    weighted_preds = tf.zeros_like(ensemble_preds[0])
    for w, pred in zip(mixture_weights, ensemble_preds):
        weighted_preds += w * pred
    return weighted_preds

# =============================================================================
# 8. Evaluate the Ensemble with Optimized Mixture Weights on the Test Set
# =============================================================================
try:
    test_loss_total = 0.0
    test_acc_total = 0.0
    num_batches = 0
    for x_batch, y_batch in test_ds:
        preds = ensemble_predict(x_batch, ensemble, final_weights)
        loss = tf.reduce_mean(tf.keras.losses.sparse_categorical_crossentropy(y_batch, preds, from_logits=True))
        acc = tf.reduce_mean(tf.cast(tf.equal(tf.argmax(preds, axis=-1, output_type=tf.int32), y_batch), tf.float32))
        test_loss_total += loss.numpy()
        test_acc_total += acc.numpy()
        num_batches += 1
    print(f"\nEnsemble Test Loss: {test_loss_total / num_batches:.4f}, "
          f"Test Accuracy: {test_acc_total / num_batches:.4f}")
except Exception as e:
    print("Error calculating test accuracy:", e)

# =============================================================================
# 9. Save the Ensemble for Future Predictions
# =============================================================================
try:
    for i, model in enumerate(ensemble):
        save_path = f'ensemble_model_candidate_{i+1}.h5'
        model.save(save_path)
        print(f"Saved candidate {i+1} to {save_path}")
    print("Ensemble saved successfully.")
except Exception as e:
    print("Error saving ensemble:", e)
# =============================================================================
# 10. Save yourself some money
# =============================================================================
from google.colab import runtime
runtime.unassign()

Global mixed precision policy: <DTypePolicy "mixed_float16">
Test tensor c dtype (should be float16): <dtype: 'float16'>
Running on GPU with Mixed Precision and XLA enabled.

--- Testing Convex Mixture Optimization ---
Initial dummy mixture loss: 2.5340755
Epoch 1: dummy loss 2.5340754985809326
Epoch 2: dummy loss 2.5336976051330566
Epoch 3: dummy loss 2.5333197116851807
Epoch 4: dummy loss 2.532942295074463
Epoch 5: dummy loss 2.532565116882324
Epoch 6: dummy loss 2.5321884155273438
Epoch 7: dummy loss 2.5318121910095215
Epoch 8: dummy loss 2.531435966491699
Epoch 9: dummy loss 2.5310604572296143
Epoch 10: dummy loss 2.5306851863861084
Final dummy mixture weights: [0.33554775 0.32890514 0.33554715]
--- Convex Mixture Optimization Test Completed ---


--- RL Iteration 1/10 ---

Candidate 1: layers = 2, dropout_rate = 0.26


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_1 (InputLayer)      │ (None, 32, 32, 3)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_flip_1 (RandomFlip)      │ (None, 32, 32, 3)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ random_translation_1            │ (None, 32, 32, 3)      │             0 │
│ (RandomTranslation)             │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 32, 32, 188)    │         5,264 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 32, 32, 188)    │           752 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_1 (Activation)       │ (None, 32, 32, 188)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 32, 32, 188)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 16, 16, 188)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_3 (Flatten)             │ (None, 48128)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ cast_1 (Cast)                   │ (None, 48128)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_11 (Dense)                │ (None, 10)             │       481,290 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 487,306 (1.86 MB)

 Trainable params: 486,930 (1.86 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_48      │ (None, 32, 32, 3) │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_flip_47      │ (None, 32, 32, 3) │          0 │ input_layer_48[0… │
│ (RandomFlip)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_translation… │ (None, 32, 32, 3) │          0 │ random_flip_47[0… │
│ (RandomTranslation) │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_496 (Conv2D) │ (None, 32, 32,    │      2,968 │ random_translati… │
│                     │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 32, 32,    │        424 │ conv2d_496[0][0]  │
│ (BatchNormalizatio… │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_397      │ (None, 32, 32,    │          0 │ batch_normalizat… │
│ (Activation)        │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_397         │ (None, 32, 32,    │          0 │ activation_397[0… │
│ (Dropout)           │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_497 (Conv2D) │ (None, 32, 32,    │    101,230 │ dropout_397[0][0] │
│                     │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 32, 32,    │        424 │ conv2d_497[0][0]  │
│ (BatchNormalizatio… │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_498 (Conv2D) │ (None, 32, 32,    │        424 │ random_translati… │
│                     │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_99 (Add)        │ (None, 32, 32,    │          0 │ batch_normalizat… │
│                     │ 106)              │            │ conv2d_498[0][0]  │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_398      │ (None, 32, 32,    │          0 │ add_99[0][0]      │
│ (Activation)        │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_398         │ (None, 32, 32,    │          0 │ activation_398[0… │
│ (Dropout)           │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d_184   │ (None, 16, 16,    │          0 │ dropout_398[0][0] │
│ (MaxPooling2D)      │ 106)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_499 (Conv2D) │ (None, 16, 16,    │    243,525 │ max_pooling2d_18… │
│                     │ 255)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 16, 16,    │      1,020 │ conv2d_499[0][0]  │
│ (BatchNormalizatio… │ 255)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_399      │ (None, 16, 16,    │          0 │ batch_normalizat

 Total params: 2,201,147 (8.40 MB)

 Trainable params: 2,197,361 (8.38 MB)

 Non-trainable params: 3,786 (14.79 KB)

Training candidate model for up to 440 epochs with early stopping...
Epoch 1/440
352/352 ━━━━━━━━━━━━━━━━━━━━ 40s 37ms/step - accuracy: 0.2353 - loss: 2.2182 - val_accuracy: 0.0990 - val_loss: 3.2375 - learning_rate: 9.5000e-04
Epoch 2/440
352/352 ━━━━━━━━━━━━━━━━━━━━ 30s 85ms/step - accuracy: 0.4800 - loss: 1.5502 - val_accuracy: 0.4286 - val_loss: 1.8947 - learning_rate: 9.0250e-04
Epoch 3/440
352/352 ━━━━━━━━━━━━━━━━━━━━ 8s 23ms/step - accuracy: 0.5906 - loss: 1.2879 - val_accuracy: 0.5862 - val_loss: 1.3742 - learning_rate: 8.5737e-04
Epoch 4/440
352/352 ━━━━━━━━━━━━━━━━━━━━ 8s 23ms/step - accuracy: 0.6559 - loss: 1.1354 - val_accuracy: 0.6340 - val_loss: 1.2114 - learning_rate: 8.1451e-04
Epoch 5/440
352/352 ━━━━━━━━━━━━━━━━━━━━ 8s 23ms/step - accuracy: 0.6956 - loss: 1.0360 - val_accuracy: 0.7052 - val_loss: 1.0093 - learning_rate: 7.7378e-04
Epoch 6/440
352/352 ━━━━━━━━━━━━━━━━━━━━ 8s 23ms/step - accuracy: 0.7255 - loss: 0.9654 - val_accuracy: 0.6998 - val_loss: 1.0827 - learnin